In [137]:
import pandas as pd
import xml.etree.ElementTree as et

import spacy

from collections import defaultdict
from tqdm import tqdm

from spacy.lang.en.stop_words import STOP_WORDS

from spacy.lang.char_classes import ALPHA, ALPHA_LOWER, ALPHA_UPPER
from spacy.lang.char_classes import CONCAT_QUOTES, LIST_ELLIPSES, LIST_ICONS
from spacy.util import compile_infix_regex

import sys; sys.executable

'/Users/xu081/Documents/trec_t2/venv/bin/python3'

In [21]:
df = pd.read_pickle("../data/trials_topics_combined_all_years.pickle")
df["brief_t_and_s"] = df["brief_title"] + " " + df["brief_summary"]
df["doc_id"] = df["year"].astype(str) + "_" + df["topic"].astype(str) + "_" + df["id"]
print(df.shape)
df.head()

(40203, 25)


score           id                                      brief_summary  \
0    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
1    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
2    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
3    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
4    1.0  NCT01226147  An open-label study to evaluate the efficacy a...   

                                         brief_title minimum_age  gender  \
0  EUS-guided Fine Needle Biopsy With a New Core ...        6570    male   
1  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
2  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
3  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
4  Efficacy and Safety of Tamibarotene(AM80) for ...        7300  female   

                                     primary_outcome  \
0  Sampling Adequacy at time of procedure The abi...   
1  Sampling Adequacy at time of procedure The abi...   
2  Sampling Adequacy at time of procedure The abi...   
3  Sampling Adequacy at time of procedure The abi...   
4  Renal Function 24 weeks Urinary Protein values...   

                                detailed_description  \
0  Background: Endoscopic ultrasound (EUS) is a w...   
1  Background: Endoscopic ultrasound (EUS) is a w...   
2  Background: Endoscopic ultrasound (EUS) is a w...   
3  Background: Endoscopic ultrasound (EUS) is a w...   
4  Tamibarotene is a synthetic retinoid presently...   

                                            keywords  \
0  Endoscopic Ultrasound Fine needle aspiration F...   
1  Endoscopic Ultrasound Fine needle aspiration F...   
2  Endoscopic Ultrasound Fine needle aspiration F...   
3  Endoscopic Ultrasound Fine needle aspiration F...   
4          Lupus Nephritis SLE retinoid tamibarotene   

                                      official_title  ...  \
0  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
1  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
2  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
3  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
4                                                     ...   

                                           exclusion topic  _ label  \
0  - No detectable lesion - lesion inaccessible t...    18  0     0   
1  - No detectable lesion - lesion inaccessible t...    27  0     0   
2  - No detectable lesion - lesion inaccessible t...    28  0     0   
3  - No detectable lesion - lesion inaccessible t...    30  0     0   
4  - Pregnant or breastfeeding female patients - ...     7  0     0   

                            disease                gene   age  year  \
0                 Pancreatic cancer  CDK6 Amplification  None  2017   
1         Pancreatic adenocarcinoma          KRAS, TP53  None  2017   
2  Pancreatic ductal adenocarcinoma               ERBB3  None  2017   
3         Pancreatic adenocarcinoma     RB1, TP53, KRAS  None  2017   
4                       Lung cancer        EGFR (L858R)  None  2017   

                                       brief_t_and_s               doc_id  
0  EUS-guided Fine Needle Biopsy With a New Core ...  2017_18_NCT01774162  
1  EUS-guided Fine Needle Biopsy With a New Core ...  2017_27_NCT01774162  
2  EUS-guided Fine Needle Biopsy With a New Core ...  2017_28_NCT01774162  
3  EUS-guided Fine Needle Biopsy With a New Core ...  2017_30_NCT01774162  
4  Efficacy and Safety of Tamibarotene(AM80) for ...   2017_7_NCT01226147  

[5 rows x 25 columns]

In [169]:
df.year.unique()

array([2017, 2018, 2019])

In [22]:
type(df["brief_t_and_s"][0].split(" ")) == list

True

In [23]:
def parse_topics(topics_path, topics_xml):
    """ Specifc XML parsing of topics file for TREC PM dataset """
    topics_xml = et.parse(f"{topics_path}/{topics_xml}")
    topics_root = topics_xml.getroot()
    topic_root = topics_root

    topics_dict = defaultdict(list)
    for child in topics_root:
        feature_arr = []
        topic_num = child.attrib["number"]
        for cc in child:
            feature_arr.append(cc.text)
        if int(topic_num) % 10 == 0:
            print(f"child.attrib[\"number\"]: {topic_num}")
            print(feature_arr)
        topics_dict[int(topic_num)] = feature_arr

    return topics_dict

In [24]:
YEAR = 2017
topics_path = f"../data/pm_labels_{YEAR}"
topics_xml = f"topics{YEAR}.xml"

tops = parse_topics(topics_path, topics_xml)

child.attrib["number"]: 10
['Lung adenocarcinoma', 'KRAS (G12C)', '61-year-old female', 'Hypertension, Hypercholesterolemia']
child.attrib["number"]: 20
['Liposarcoma', 'MDM2 Amplification', '26-year-old male', 'None']
child.attrib["number"]: 30
['Pancreatic adenocarcinoma', 'RB1, TP53, KRAS', '57-year-old female', 'None']


In [25]:
tops

defaultdict(list,
            {1: ['Liposarcoma',
              'CDK4 Amplification',
              '38-year-old male',
              'GERD'],
             2: ['Colon cancer',
              'KRAS (G13D), BRAF (V600E)',
              '52-year-old male',
              'Type II Diabetes, Hypertension'],
             3: ['Meningioma',
              'NF2 (K322), AKT1(E17K)',
              '45-year-old female',
              'None'],
             4: ['Breast cancer',
              'FGFR1 Amplification, PTEN (Q171)',
              '67-year-old female',
              'Depression, Hypertension, Heart Disease'],
             5: ['Melanoma',
              'BRAF (V600E), CDKN2A Deletion',
              '45-year-old female',
              'None'],
             6: ['Melanoma',
              'NRAS (Q61K)',
              '55-year-old male',
              'Hypertension'],
             7: ['Lung cancer', 'EGFR (L858R)', '50-year-old female', 'Lupus'],
             8: ['Lung cancer',
              'EML4-

In [83]:
sp = spacy.load('en_core_web_sm')

# https://spacy.io/usage/linguistic-features#native-tokenizer-additions
# https://github.com/explosion/spaCy/blob/master/spacy/util.py
# https://github.com/explosion/spaCy/blob/master/spacy/lang/punctuation.py
# infixes = list(sp.Defaults.infixes) # get the default infixes but best to use 

infixes = (
    LIST_ELLIPSES
    + LIST_ICONS
    + [
        r"(?<=[0-9])[+\-\*^](?=[0-9-])",
        r"(?<=[{al}{q}])\.(?=[{au}{q}])".format(
            al=ALPHA_LOWER, au=ALPHA_UPPER, q=CONCAT_QUOTES
        ),
        r"(?<=[{a}]),(?=[{a}])".format(a=ALPHA),
        # EDIT: commented out regex that splits on hyphens between letters:
        #r"(?<=[{a}])(?:{h})(?=[{a}])".format(a=ALPHA, h=HYPHENS),
        r"(?<=[{a}0-9])[:<>=/](?=[{a}])".format(a=ALPHA),
    ]
)

infix_re = compile_infix_regex(infixes)
sp.tokenizer.infix_finditer = infix_re.finditer

In [111]:
list(sp.Defaults.infixes)[6]

'(?<=[A-Za-z\\uFF21-\\uFF3A\\uFF41-\\uFF5A\\u00C0-\\u00D6\\u00D8-\\u00F6\\u00F8-\\u00FF\\u0100-\\u017F\\u0180-\\u01BF\\u01C4-\\u024F\\u2C60-\\u2C7B\\u2C7E\\u2C7F\\uA722-\\uA76F\\uA771-\\uA787\\uA78B-\\uA78E\\uA790-\\uA7B9\\uA7FA\\uAB30-\\uAB5A\\uAB60-\\uAB64\\u0250-\\u02AF\\u1D00-\\u1D25\\u1D6B-\\u1D77\\u1D79-\\u1D9A\\u1E00-\\u1EFFёа-яЁА-ЯәөүҗңһӘӨҮҖҢҺα-ωάέίόώήύΑ-ΩΆΈΊΌΏΉΎа-щюяіїєґА-ЩЮЯІЇЄҐ\\u0980-\\u09FF\\u0591-\\u05F4\\uFB1D-\\uFB4F\\u0620-\\u064A\\u066E-\\u06D5\\u06E5-\\u06FF\\u0750-\\u077F\\u08A0-\\u08BD\\uFB50-\\uFBB1\\uFBD3-\\uFD3D\\uFD50-\\uFDC7\\uFDF0-\\uFDFB\\uFE70-\\uFEFC\\U0001EE00-\\U0001EEBB\\u0D80-\\u0DFF\\u0900-\\u097F\\u0C80-\\u0CFF\\u0B80-\\u0BFF\\u0C00-\\u0C7F\\uAC00-\\uD7AF\\u1100-\\u11FF])(?:-|–|—|--|---|——|~)(?=[A-Za-z\\uFF21-\\uFF3A\\uFF41-\\uFF5A\\u00C0-\\u00D6\\u00D8-\\u00F6\\u00F8-\\u00FF\\u0100-\\u017F\\u0180-\\u01BF\\u01C4-\\u024F\\u2C60-\\u2C7B\\u2C7E\\u2C7F\\uA722-\\uA76F\\uA771-\\uA787\\uA78B-\\uA78E\\uA790-\\uA7B9\\uA7FA\\uAB30-\\uAB5A\\uAB60-\\uAB64\\u0250

In [139]:
def build_field_dict(topics_dict, idx, spacy_lm):
    """
    Grab topics_dict, which has format
        {
        1: [<gene>, <disease>, <age and gender>, <other>],
        2: [<gene>, <disease>, <age and gender>, <other>],
        ...
        n: [<gene>, <disease>, <age and gender>, <other>]
    }
    and return a one-hot vector of unique words along with an idx mapping
    to the position of the words
    """
    
    i = 0
    unique_tokens = {}
    for key, value in topics_dict.items():
        print(f"key: {key}\nvalue: {value}")
        field_tokens_spacy = [w.lemma_ for w in spacy_lm(value[idx])]
        field_tokens = [process_field_text(t) for t in field_tokens_spacy]
        for t in field_tokens:
            try:
                unique_tokens[t]
            except KeyError:
                if len(t) > 0:
                    unique_tokens[t] = i
                    i += 1
    return unique_tokens

def build_field_qe_dict(df_col, stop_words, spacy_lm):
    """
    Grab pd.Series with
        [
        word1, word2, ..., word_k
    ]
    and return a one-hot vector of unique 
    words along with an idx mapping to the position of the words.
    """
    
    i = 0
    unique_tokens = {}
    for col in df_col:
        text = " ".join(col)
        print(f"text: {text}")
        field_tokens_spacy = [w.lemma_ for w in spacy_lm(text)]
        field_tokens = [process_field_text(t) for t in field_tokens_spacy]
        for t in field_tokens:
            try:
                unique_tokens[t]
            except KeyError:
                if (len(t) > 1) and (t not in stop_words):
                    unique_tokens[t] = i
                    i += 1
    return unique_tokens

def process_field_text(token, spacy_lm=sp):
#     print(token)
    token = token.strip()
    token = token.replace("(", "")
    token = token.replace(")", "")
    token = token.replace(",", "")
    token = token.replace(";", "")
    token = token.replace(":", "")
    token = token.lower()
#     token = lemmatise(token, spacy_lm)
    return token

def lemmatise(token, spacy_lm):
    # Returns a Spacy document, which is special
    # We however, only need the token.
    if len(token) == 0:
#         print(f"token is: {token}")
#         print("len of token is zero")
        token = "none"
    text_sp = spacy_lm(token)
    if len(text_sp.text) == 0:
        print(text_sp.text)
    return text_sp[0].lemma_

def count_field(query_field, field_dict, spacy_lm):
    """
    Given a query field (e.g. gene), count the exact matches for
    each gene that appears in the field_dict.
    
    The field_token_arr is a one-hot vector encoding for each word. 
    Luckily there isn't too many as we are purely focusing on genes.
    """
    print_flag = False
    
    field_token_arr = [0]*(len(field_dict.keys()))
                           
    field_tokens_spacy = [w.lemma_ for w in spacy_lm(query_field)]
    query_field = [process_field_text(t) for t in field_tokens_spacy]
#     print(f"query_field: {query_field}")
    for t in query_field:
#         print(f"t: {t}")
#         print(field_dict[t])
        if t in field_dict.keys():
            print_flag = True
            field_token_arr[field_dict[t]] += 1
            
    if print_flag:
#         print(f"sum of counts is: {sum(field_token_arr)}")
#         print(f"processed query_field is:\n{query_field}")
        print_flag = False
    return field_token_arr

def build_field_count(df_col_text, df_col_id, field_dict, spacy_lm):
    """
    word_count_vec_dict = {
        "2017_1_NCT01774162": [0, 0, 1, ..., 0],
        "2017_1_NCT..."     : [1, 1, 1, ..., 0],
        ...
        "2019_40_NCT..."    : [0, 1, 0, ..., 0],
    }
    """
    word_count_vec_dict = {}
    for i in tqdm(range(len(df_col_text))):
#         print(f"index of df is: {i}")
        count_vec = count_field(df_col_text[i], field_dict, spacy_lm)
        word_count_vec_dict[df_col_id[i]] = count_vec
    
    return word_count_vec_dict

## Building gene vector

In [27]:
gene2id_dict = build_field_dict(topics_dict=tops, idx=1, spacy_lm=sp)
gene2id_dict

key: 1
value: ['Liposarcoma', 'CDK4 Amplification', '38-year-old male', 'GERD']
key: 2
value: ['Colon cancer', 'KRAS (G13D), BRAF (V600E)', '52-year-old male', 'Type II Diabetes, Hypertension']
key: 3
value: ['Meningioma', 'NF2 (K322), AKT1(E17K)', '45-year-old female', 'None']
key: 4
value: ['Breast cancer', 'FGFR1 Amplification, PTEN (Q171)', '67-year-old female', 'Depression, Hypertension, Heart Disease']
key: 5
value: ['Melanoma', 'BRAF (V600E), CDKN2A Deletion', '45-year-old female', 'None']
key: 6
value: ['Melanoma', 'NRAS (Q61K)', '55-year-old male', 'Hypertension']
key: 7
value: ['Lung cancer', 'EGFR (L858R)', '50-year-old female', 'Lupus']
key: 8
value: ['Lung cancer', 'EML4-ALK Fusion transcript', '52-year-old male', 'Hypertension, Osteoarthritis']
key: 9
value: ['Gastrointestinal stromal tumor', 'KIT Exon 9 (A502_Y503dup)', '49-year-old female', 'None']
key: 10
value: ['Lung adenocarcinoma', 'KRAS (G12C)', '61-year-old female', 'Hypertension, Hypercholesterolemia']
key: 11
v

{'cdk4': 0,
 'amplification': 1,
 'kras': 2,
 'g13d': 3,
 'braf': 4,
 'v600e': 5,
 'nf2': 6,
 'k322': 7,
 'akt1e17': 8,
 'k': 9,
 'fgfr1': 10,
 'pten': 11,
 'q171': 12,
 'cdkn2a': 13,
 'deletion': 14,
 'nras': 15,
 'q61': 16,
 'egfr': 17,
 'l858r': 18,
 'eml4-alk': 19,
 'fusion': 20,
 'transcript': 21,
 'kit': 22,
 'exon': 23,
 '9': 24,
 'a502_y503dup': 25,
 'g12c': 26,
 'pik3ca': 27,
 'e545': 28,
 'brca2': 29,
 'idh1': 30,
 'r132h': 31,
 'stk11': 32,
 'inactivating': 33,
 'cdk6': 34,
 'mdm2': 35,
 'alk': 36,
 'erbb2': 37,
 'loss': 38,
 'ntrk1': 39,
 'met': 40,
 'tp53': 41,
 'erbb3': 42,
 'rb1': 43}

In [28]:
len(gene2id_dict.keys())

44

In [29]:
len(set(gene2id_dict.values()))

44

In [30]:
df_rel = df[df["label"] == 1]
df_rel.head()[["id", "brief_t_and_s", "label"]]

id                                      brief_t_and_s  label
30  NCT02465060  NCI-MATCH: Targeted Therapy Directed by Geneti...      1
33  NCT02465060  NCI-MATCH: Targeted Therapy Directed by Geneti...      1
36  NCT00818441  Dacomitinib (PF-00299804) As A Single Oral Age...      1
57  NCT01050322  Safety Study in Subjects With Metastatic Breas...      1
67  NCT02040870  LDK378 in Adult Chinese Patients With ALK-rear...      1

In [31]:
df_rel["brief_t_and_s"][30]

"NCI-MATCH: Targeted Therapy Directed by Genetic Testing in Treating Patients With Advanced Refractory Solid Tumors, Lymphomas, or Multiple Myeloma This phase II trial studies how well treatment that is directed by genetic testing works in patients with solid tumors or lymphomas that have progressed following at least one line of standard treatment or for which no agreed upon treatment approach exists. Genetic tests look at the unique genetic material (genes) of patients' tumor cells. Patients with genetic abnormalities (such as mutations, amplifications, or translocations) may benefit more from treatment which targets their tumor's particular genetic abnormality. Identifying these genetic abnormalities first may help doctors plan better treatment for patients with solid tumors, lymphomas, or multiple myeloma."

In [32]:
for i in tqdm(range(df.iloc[:50].shape[0])):
    print(f"index of df is: {i}")
#     print(df["gene"][i])
    count_field(df["brief_t_and_s"][i], gene2id_dict, sp)


  6%|▌         | 3/50 [00:00<00:01, 23.95it/s]

index of df is: 0
index of df is: 1
index of df is: 2
index of df is: 3
index of df is: 4
index of df is: 5
index of df is: 6
index of df is: 7



 26%|██▌       | 13/50 [00:00<00:01, 31.93it/s]

index of df is: 8
index of df is: 9
index of df is: 10
index of df is: 11
index of df is: 12
index of df is: 13
index of df is: 14
index of df is: 15
index of df is: 16
index of df is: 17
index of df is: 18



 48%|████▊     | 24/50 [00:00<00:00, 39.24it/s]

...

index of df is: 30
index of df is: 31
index of df is: 32
index of df is: 33
index of df is: 34
index of df is: 35
index of df is: 36



 90%|█████████ | 45/50 [00:01<00:00, 41.98it/s]

index of df is: 37
index of df is: 38
index of df is: 39
index of df is: 40
index of df is: 41
index of df is: 42
index of df is: 43
index of df is: 44
index of df is: 45
index of df is: 46



100%|██████████| 50/50 [00:01<00:00, 43.60it/s]

index of df is: 47
index of df is: 48
index of df is: 49


In [33]:
gene_count_vec_dict = build_field_count(
    df_col_text=df["brief_t_and_s"],
    df_col_id=df["doc_id"], 
    field_dict=gene2id_dict, spacy_lm=sp
)


  2%|▏         | 902/40203 [00:19<13:21, 49.03it/s]


  4%|▍         | 1704/40203 [00:39<20:24, 31.45it/s]


  7%|▋         | 2619/40203 [00:58<12:34, 49.78it/s]


  9%|▉         | 3556/40203 [01:17<14:44, 41.45it/s]


 11%|█         | 4470/40203 [01:37<12:49, 46.42it/s]


...

 92%|█████████▏| 36924/40203 [12:35<00:57, 57.21it/s]


 94%|█████████▍| 37859/40203 [12:53<00:37, 62.21it/s]


 97%|█████████▋| 38834/40203 [13:12<00:26, 50.87it/s]


 99%|█████████▉| 39805/40203 [13:30<00:07, 54.31it/s]


100%|██████████| 40203/40203 [13:37<00:00, 49.16it/s]


In [34]:
gene_path = "../data/aspect_data/sample/gene_word_vec.pickle"
pd.to_pickle(gene_count_vec_dict, gene_path)

In [35]:
gene_count_vec_dict

{'2017_18_NCT01774162': [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 '2017_27_NCT01774162': [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 '2017_28_NCT01774162': [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 '2017_30_NCT01774162': [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0],
 '2017_7_NCT01226147': [

## Building disease vector

In [36]:
disease2id_dict = build_field_dict(topics_dict=tops, idx=0, spacy_lm=sp)
disease2id_dict

key: 1
value: ['Liposarcoma', 'CDK4 Amplification', '38-year-old male', 'GERD']
key: 2
value: ['Colon cancer', 'KRAS (G13D), BRAF (V600E)', '52-year-old male', 'Type II Diabetes, Hypertension']
key: 3
value: ['Meningioma', 'NF2 (K322), AKT1(E17K)', '45-year-old female', 'None']
key: 4
value: ['Breast cancer', 'FGFR1 Amplification, PTEN (Q171)', '67-year-old female', 'Depression, Hypertension, Heart Disease']
key: 5
value: ['Melanoma', 'BRAF (V600E), CDKN2A Deletion', '45-year-old female', 'None']
key: 6
value: ['Melanoma', 'NRAS (Q61K)', '55-year-old male', 'Hypertension']
key: 7
value: ['Lung cancer', 'EGFR (L858R)', '50-year-old female', 'Lupus']
key: 8
value: ['Lung cancer', 'EML4-ALK Fusion transcript', '52-year-old male', 'Hypertension, Osteoarthritis']
key: 9
value: ['Gastrointestinal stromal tumor', 'KIT Exon 9 (A502_Y503dup)', '49-year-old female', 'None']
key: 10
value: ['Lung adenocarcinoma', 'KRAS (G12C)', '61-year-old female', 'Hypertension, Hypercholesterolemia']
key: 11
v

{'liposarcoma': 0,
 'colon': 1,
 'cancer': 2,
 'meningioma': 3,
 'breast': 4,
 'melanoma': 5,
 'lung': 6,
 'gastrointestinal': 7,
 'stromal': 8,
 'tumor': 9,
 'adenocarcinoma': 10,
 'gastric': 11,
 'cholangiocarcinoma': 12,
 'cervical': 13,
 'pancreatic': 14,
 'prostate': 15,
 'colorectal': 16,
 'ductal': 17,
 'ampullary': 18,
 'carcinoma': 19}

In [37]:
disease_count_vec_dict = build_field_count(
    df_col_text=df["brief_t_and_s"],
    df_col_id=df["doc_id"],
    field_dict=disease2id_dict, spacy_lm=sp
)


  3%|▎         | 1032/40203 [00:19<14:45, 44.22it/s]


  5%|▌         | 2071/40203 [00:37<11:51, 53.58it/s]


  8%|▊         | 3131/40203 [00:56<14:45, 41.87it/s]


 10%|█         | 4178/40203 [01:15<10:01, 59.85it/s]


 13%|█▎        | 5230/40203 [01:34<13:33, 43.00it/s]


...

 92%|█████████▏| 36859/40203 [11:06<01:09, 48.34it/s]


 94%|█████████▍| 37784/40203 [11:25<01:00, 39.97it/s]


 96%|█████████▋| 38763/40203 [11:43<00:33, 42.99it/s]


 99%|█████████▊| 39691/40203 [12:02<00:11, 44.20it/s]


100%|██████████| 40203/40203 [12:11<00:00, 54.95it/s]


In [38]:
disease_path = "../data/aspect_data/sample/disease_word_vec.pickle"
pd.to_pickle(disease_count_vec_dict, disease_path)

## QE DataFrame

In [153]:
df_qe = pd.read_pickle("../data/trials_topics_combined_all_years_qe.pickle")
df_qe["brief_t_and_s"] = df_qe["brief_title"] + " " + df_qe["brief_summary"]
df_qe["doc_id"] = df["year"].astype(str) + "_" + df_qe["topic"].astype(str) + "_" + df_qe["id"]
print(df_qe.shape)
df_qe.head()

(40203, 27)


score           id                                      brief_summary  \
0    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
1    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
2    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
3    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
4    1.0  NCT01226147  An open-label study to evaluate the efficacy a...   

                                         brief_title minimum_age  gender  \
0  EUS-guided Fine Needle Biopsy With a New Core ...        6570    male   
1  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
2  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
3  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
4  Efficacy and Safety of Tamibarotene(AM80) for ...        7300  female   

                                     primary_outcome  \
0  Sampling Adequacy at time of procedure The abi...   
1  Sampling Adequacy at time of procedure The abi...   
2  Sampling Adequacy at time of procedure The abi...   
3  Sampling Adequacy at time of procedure The abi...   
4  Renal Function 24 weeks Urinary Protein values...   

                                detailed_description  \
0  Background: Endoscopic ultrasound (EUS) is a w...   
1  Background: Endoscopic ultrasound (EUS) is a w...   
2  Background: Endoscopic ultrasound (EUS) is a w...   
3  Background: Endoscopic ultrasound (EUS) is a w...   
4  Tamibarotene is a synthetic retinoid presently...   

                                            keywords  \
0  Endoscopic Ultrasound Fine needle aspiration F...   
1  Endoscopic Ultrasound Fine needle aspiration F...   
2  Endoscopic Ultrasound Fine needle aspiration F...   
3  Endoscopic Ultrasound Fine needle aspiration F...   
4          Lupus Nephritis SLE retinoid tamibarotene   

                                      official_title  ...  _ label  \
0  Endoscopic Ultrasound Guided Fine Needle Biops...  ...  0     0   
1  Endoscopic Ultrasound Guided Fine Needle Biops...  ...  0     0   
2  Endoscopic Ultrasound Guided Fine Needle Biops...  ...  0     0   
3  Endoscopic Ultrasound Guided Fine Needle Biops...  ...  0     0   
4                                                     ...  0     0   

                            disease                gene   age  year  \
0                 Pancreatic cancer  CDK6 Amplification  None  2017   
1         Pancreatic adenocarcinoma          KRAS, TP53  None  2017   
2  Pancreatic ductal adenocarcinoma               ERBB3  None  2017   
3         Pancreatic adenocarcinoma     RB1, TP53, KRAS  None  2017   
4                       Lung cancer        EGFR (L858R)  None  2017   

                                      d_and_g  \
0       Pancreatic cancer, CDK6 Amplification   
1       Pancreatic adenocarcinoma, KRAS, TP53   
2     Pancreatic ductal adenocarcinoma, ERBB3   
3  Pancreatic adenocarcinoma, RB1, TP53, KRAS   
4                   Lung cancer, EGFR (L858R)   

                                              qe_all  \
0  [Pancreatic cancer, CDK6 Amplification, cyclin...   
1  [Pancreatic adenocarcinoma, KRAS, TP53, KRAS p...   
2  [Pancreatic ductal adenocarcinoma, ERBB3, erb-...   
3  [Pancreatic adenocarcinoma, RB1, TP53, KRAS, R...   
4  [Lung cancer, EGFR (L858R), epidermal growth f...   

                                       brief_t_and_s               doc_id  
0  EUS-guided Fine Needle Biopsy With a New Core ...  2017_18_NCT01774162  
1  EUS-guided Fine Needle Biopsy With a New Core ...  2017_27_NCT01774162  
2  EUS-guided Fine Needle Biopsy With a New Core ...  2017_28_NCT01774162  
3  EUS-guided Fine Needle Biopsy With a New Core ...  2017_30_NCT01774162  
4  Efficacy and Safety of Tamibarotene(AM80) for ...   2017_7_NCT01226147  

[5 rows x 27 columns]

In [154]:
# See snomed_ncbi_qe.py for the indexing

df_qe["gene_qe"] = df_qe["qe_all"].apply(lambda x: x[1:5])
df_qe["disease_qe"] = df_qe["qe_all"].apply(lambda x: [x[0]] + x[5:])

In [167]:
df_qe_unique_gd = df_qe.drop_duplicates(subset=["year", "topic"]).reset_index(drop=True)
print(df_qe_unique_gd.shape)
df_qe_unique_gd.head()

(117, 29)


score           id                                      brief_summary  \
0    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
1    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
2    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
3    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
4    1.0  NCT01226147  An open-label study to evaluate the efficacy a...   

                                         brief_title minimum_age  gender  \
0  EUS-guided Fine Needle Biopsy With a New Core ...        6570    male   
1  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
2  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
3  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
4  Efficacy and Safety of Tamibarotene(AM80) for ...        7300  female   

                                     primary_outcome  \
0  Sampling Adequacy at time of procedure The abi...   
1  Sampling Adequacy at time of procedure The abi...   
2  Sampling Adequacy at time of procedure The abi...   
3  Sampling Adequacy at time of procedure The abi...   
4  Renal Function 24 weeks Urinary Protein values...   

                                detailed_description  \
0  Background: Endoscopic ultrasound (EUS) is a w...   
1  Background: Endoscopic ultrasound (EUS) is a w...   
2  Background: Endoscopic ultrasound (EUS) is a w...   
3  Background: Endoscopic ultrasound (EUS) is a w...   
4  Tamibarotene is a synthetic retinoid presently...   

                                            keywords  \
0  Endoscopic Ultrasound Fine needle aspiration F...   
1  Endoscopic Ultrasound Fine needle aspiration F...   
2  Endoscopic Ultrasound Fine needle aspiration F...   
3  Endoscopic Ultrasound Fine needle aspiration F...   
4          Lupus Nephritis SLE retinoid tamibarotene   

                                      official_title  ...  \
0  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
1  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
2  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
3  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
4                                                     ...   

                            disease                gene   age  year  \
0                 Pancreatic cancer  CDK6 Amplification  None  2017   
1         Pancreatic adenocarcinoma          KRAS, TP53  None  2017   
2  Pancreatic ductal adenocarcinoma               ERBB3  None  2017   
3         Pancreatic adenocarcinoma     RB1, TP53, KRAS  None  2017   
4                       Lung cancer        EGFR (L858R)  None  2017   

                                      d_and_g  \
0       Pancreatic cancer, CDK6 Amplification   
1       Pancreatic adenocarcinoma, KRAS, TP53   
2     Pancreatic ductal adenocarcinoma, ERBB3   
3  Pancreatic adenocarcinoma, RB1, TP53, KRAS   
4                   Lung cancer, EGFR (L858R)   

                                              qe_all  \
0  [Pancreatic cancer, CDK6 Amplification, cyclin...   
1  [Pancreatic adenocarcinoma, KRAS, TP53, KRAS p...   
2  [Pancreatic ductal adenocarcinoma, ERBB3, erb-...   
3  [Pancreatic adenocarcinoma, RB1, TP53, KRAS, R...   
4  [Lung cancer, EGFR (L858R), epidermal growth f...   

                                       brief_t_and_s               doc_id  \
0  EUS-guided Fine Needle Biopsy With a New Core ...  2017_18_NCT01774162   
1  EUS-guided Fine Needle Biopsy With a New Core ...  2017_27_NCT01774162   
2  EUS-guided Fine Needle Biopsy With a New Core ...  2017_28_NCT01774162   
3  EUS-guided Fine Needle Biopsy With a New Core ...  2017_30_NCT01774162   
4  Efficacy and Safety of Tamibarotene(AM80) for ...   2017_7_NCT01226147   

                                             gene_qe  \
0  [CDK6 Amplification, cyclin dependent kinase 6...   
1  [KRAS, TP53, KRAS proto-oncogene, GTPase tumor...   
2  [ERBB3, erb-b2 rec

In [164]:
df_qe_unique_gd.tail()

score           id                                      brief_summary  \
27280    1.0  NCT01059188  RATIONALE: Monoclonal antibodies, such as cetu...   
27287    1.0  NCT02315625  Background: - Neuroendocrine tumors (NETs) com...   
27299    1.0  NCT03206073  Background: - Immune-based approaches in color...   
27313    1.0  NCT02110563  The purpose of this study is to assess the saf...   
27496    1.0  NCT00718562  This study will evaluate the efficacy and safe...   

                                             brief_title minimum_age  gender  \
27280  Neo-adjuvant Treatment in Non-Small Cell Lung ...        6570  female   
27287  Study of Mutation-Targeted Therapy With Suniti...        6570    male   
27299  A Phase I/II Study of Pexa-Vec Oncolytic Virus...        6570    male   
27313  Phase I, Multicenter, Dose Escalation Study of...        6570    male   
27496  Efficacy and Safety of AMN107 in Patients With...        7300  female   

                                         primary_outcome  \
27280  Progression-free survival at 1 year (+/- 1 month)   
27287  Progression Free Survival (PFS) at progression...   
27299  safety, tolerability and feasibility of Pexa-V...   
27313  Number of patients with adverse events as a me...   
27496  Disease Control Rate (DCR) in all patients wit...   

                                    detailed_description  \
27280  OBJECTIVES: - To evaluate the efficacy and saf...   
27287  Background: - Neuroendocrine tumors (NETs) of ...   
27299  Background: - Immune-based approaches in color...   
27313  In this first-in human study, DCR-MYC will be ...   
27496                                                      

                                                keywords  \
27280  stage IIIB non-small cell lung cancer adenocar...   
27287                         MEN1 VHL Neoplasm NF1 mTOR   
27299  Oncolytic Vaccinia Virus Tumor Cell Death Vira...   
27313                                                      
27496  nilotinib AMN107 Sunitinib Sunitinib malate Im...   

                                          official_title  ...  \
27280  Preoperative Chemotherapy and Radiotherapy Con...  ...   
27287  A Phase II Trial of Mutation-Targeted Therapy ...  ...   
27299  A Phase I/II Study of Pexa-Vec Oncolytic Virus...  ...   
27313  Phase I, Multicenter, Cohort Dose Escalation T...  ...   
27496  A Multi-center Phase II Study to Evaluate the ...  ...   

                              disease  \
27280                 aortic aneurysm   
27287  gastrointestinal stromal tumor   
27299                    colon cancer   
27313          malignant hyperthermia   
27496  gastrointestinal stromal tumor   

                                                    gene   age  year  \
27280                                              ACTA2  None  2019   
27287                                        KIT (V654A)  None  2019   
27299  MLH1 methylation suppression (microsatellite i...  None  2019   
27313                                               RYR1  None  2019   
27496                                     PDGFRA (D842V)  None  2019   

                                                 d_and_g  \
27280                             aortic aneurysm, ACTA2   
27287        gastrointestinal stromal tumor, KIT (V654A)   
27299  colon cancer, MLH1 methylation suppression (mi...   
27313                       malignant hyperthermia, RYR1   
27496     gastrointestinal stromal tumor, PDGFRA (D842V)   

                                                  qe_all  \
27280  [aortic aneurysm, ACTA2, actin alpha 2, smooth...   
27287  [gastrointestinal stromal tumor, KIT (V654A), ...   
27299  [colon cancer, MLH1 methylation suppression (m...   
27313  [malignant hyperthermia, RYR1, ryanodine recep...   
27496  [gastrointestinal stromal tumor, PDGFRA (D842V...   

                                           brief_t_and_s               doc_id  \
27280  Neo-adjuvant Treatment in Non-Small Cell Lung ...  2019_31_NCT01059188   
27287  

## Building gene vector QE

In [158]:
gene2id_dict = build_field_qe_dict(
    df_col=df_qe_unique_gd["gene_qe"], 
    stop_words=STOP_WORDS, spacy_lm=sp
)

text: CDK6 Amplification cyclin dependent kinase 6 MCPH12 PLSTIRE cyclin-dependent kinase 6 cell division protein kinase 6 serine/threonine-protein kinase PLSTIRE
text: KRAS, TP53 KRAS proto-oncogene, GTPase tumor protein p53 'C-K-RAS C-K-RAS CFC2 K-RAS2A K-RAS2B K-RAS4A K-RAS4B K-Ras K-Ras 2 KI-RAS KRAS1 KRAS2 NS NS3 OES RALD RASK2 c-Ki-ras c-Ki-ras2 BCC7 BMFS5 LFS1 P53 TRP53 GTPase KRas K-ras p21 protein Kirsten rat sarcoma viral oncogene homolog Kirsten rat sarcoma viral proto-oncogene PR310 c-K-ras oncogene c-Kirsten-ras protein cellular c-Ki-ras2 proto-oncogene cellular transforming proto-oncogene oncogene KRAS2 transforming protein p21 v-Ki-ras2 Kirsten rat sarcoma 2 viral oncogene homolog cellular tumor antigen p53 antigen NY-CO-13 mutant tumor protein 53 p53 tumor suppressor phosphoprotein p53 transformation-related protein 53 tumor protein 53 tumor supressor p53
text: ERBB3 erb-b2 receptor tyrosine kinase 3 ErbB-3 FERLK HER3 LCCS2 MDA-BF-1 c-erbB-3 c-erbB3 erbB3-S p180-ErbB3 p

text: BRAF (V600E) B-Raf proto-oncogene, serine/threonine kinase B-RAF1 B-raf BRAF1 NS7 RAFB1 serine/threonine-protein kinase B-raf 94 kDa B-raf protein B-Raf proto-oncogene serine/threonine-protein kinase (p94) B-Raf serine/threonine-protein murine sarcoma viral (v-raf) oncogene homolog B1 proto-oncogene B-Raf v-raf murine sarcoma viral oncogene homolog B v-raf murine sarcoma viral oncogene homolog B1
text: BRAF (V600K) B-Raf proto-oncogene, serine/threonine kinase B-RAF1 B-raf BRAF1 NS7 RAFB1 serine/threonine-protein kinase B-raf 94 kDa B-raf protein B-Raf proto-oncogene serine/threonine-protein kinase (p94) B-Raf serine/threonine-protein murine sarcoma viral (v-raf) oncogene homolog B1 proto-oncogene B-Raf v-raf murine sarcoma viral oncogene homolog B v-raf murine sarcoma viral oncogene homolog B1
text: BRAF (V600R) B-Raf proto-oncogene, serine/threonine kinase B-RAF1 B-raf BRAF1 NS7 RAFB1 serine/threonine-protein kinase B-raf 94 kDa B-raf protein B-Raf proto-oncogene serine/threoni

text: PTCH1 patched 1 BCNS NBCCS PTC PTC1 PTCH protein patched homolog 1
text: PTEN phosphatase and tensin homolog 10q23del BZS CWS1 DEC GLM2 MHAM MMAC1 PTEN1 PTENbeta TEP1 phosphatidylinositol 3,4,5-trisphosphate 3-phosphatase and dual-specificity protein phosphatase PTEN MMAC1 phosphatase and tensin homolog deleted on chromosome 10 mitochondrial PTENalpha mitochondrial phosphatase and tensin protein alpha mutated in multiple advanced cancers 1 phosphatase and tensin-like protein phosphatidylinositol-3,4,5-trisphosphate 3-phosphatase and dual-specificity protein phosphatase PTEN protein tyrosine phosphatase
text: NTRK1 neurotrophic receptor tyrosine kinase 1 MTC TRK TRK1 TRKA Trk-A p140-TrkA high affinity nerve growth factor receptor Oncogene TRK TRK1-transforming tyrosine kinase protein gp140trk neurotrophic tyrosine kinase, receptor, type 1 tropomyosin-related kinase A tyrosine kinase receptor A
text: BRAF B-Raf proto-oncogene, serine/threonine kinase B-RAF1 B-raf BRAF1 NS7 RAFB1 se

text: EZR-ROS1 fusion   
text: SCN5A sodium voltage-gated channel alpha subunit 5 CDCD2 CMD1E CMPD2 HB1 HB2 HBBD HH1 ICCD IVF LQT3 Nav1.5 PFHB1 SSS1 VF1 sodium channel protein type 5 subunit alpha cardiac tetrodotoxin-insensitive voltage-dependent sodium channel alpha subunit sodium channel protein cardiac muscle subunit alpha sodium channel, voltage-gated, type V, alpha subunit voltage-gated sodium channel subunit alpha Nav1.5
text: EGFR (D770N) epidermal growth factor receptor ERBB ERBB1 HER1 NISBD2 PIG61 mENA epidermal growth factor receptor avian erythroblastic leukemia viral (v-erb-b) oncogene homolog cell growth inhibiting protein 40 cell proliferation-inducing protein 61 epidermal growth factor receptor tyrosine kinase domain erb-b2 receptor tyrosine kinase 1 proto-oncogene c-ErbB-1 receptor tyrosine-protein kinase erbB-1
text: EGFR (T790M) epidermal growth factor receptor ERBB ERBB1 HER1 NISBD2 PIG61 mENA epidermal growth factor receptor avian erythroblastic leukemia viral (v-e

In [157]:
gene2id_dict

{'cdk6': 0,
 'amplification': 1,
 'cyclin': 2,
 'dependent': 3,
 'kinase': 4,
 'mcph12': 5,
 'plstire': 6,
 'cyclin-dependent': 7,
 'cell': 8,
 'division': 9,
 'protein': 10,
 'serine': 11,
 'threonine-protein': 12,
 'kras': 13,
 'tp53': 14,
 'proto-oncogene': 15,
 'gtpase': 16,
 'tumor': 17,
 'p53': 18,
 'c-k-ras': 19,
 'cfc2': 20,
 'k-ras2a': 21,
 'k-ras2b': 22,
 'k-ras4a': 23,
 'k-ras4b': 24,
 'k-ras': 25,
 'ki-ras': 26,
 'kras1': 27,
 'kras2': 28,
 'ns': 29,
 'ns3': 30,
 'oes': 31,
 'rald': 32,
 'rask2': 33,
 'c-ki-ras': 34,
 'c-ki-ras2': 35,
 'bcc7': 36,
 'bmfs5': 37,
 'lfs1': 38,
 'trp53': 39,
 'p21': 40,
 'kirsten': 41,
 'rat': 42,
 'sarcoma': 43,
 'viral': 44,
 'oncogene': 45,
 'homolog': 46,
 'pr310': 47,
 'c-kirsten-ras': 48,
 'cellular': 49,
 'transforming': 50,
 'transform': 51,
 'v-ki-ras2': 52,
 'antigen': 53,
 'ny-co-13': 54,
 'mutant': 55,
 '53': 56,
 'suppressor': 57,
 'phosphoprotein': 58,
 'transformation-related': 59,
 'supressor': 60,
 'erbb3': 61,
 'erb-b2': 62,
 

In [159]:
gene_count_vec_dict = build_field_count(
    df_col_text=df["brief_t_and_s"],
    df_col_id=df["doc_id"],
    field_dict=gene2id_dict, spacy_lm=sp
)


  2%|▏         | 896/40203 [00:19<12:54, 50.74it/s]


  5%|▍         | 1841/40203 [00:38<11:58, 53.39it/s]


  7%|▋         | 2825/40203 [00:57<10:25, 59.76it/s]


  9%|▉         | 3794/40203 [01:16<14:54, 40.69it/s]


 12%|█▏        | 4786/40203 [01:35<12:50, 45.95it/s]


...

 93%|█████████▎| 37306/40203 [12:12<01:16, 37.77it/s]


 95%|█████████▍| 38184/40203 [12:30<00:47, 42.11it/s]


 97%|█████████▋| 39042/40203 [12:49<00:25, 45.35it/s]


 99%|█████████▉| 39906/40203 [13:07<00:06, 49.00it/s]


100%|██████████| 40203/40203 [13:13<00:00, 50.64it/s]


In [160]:
gene_path = "../data/aspect_data/sample/gene_qe_word_vec.pickle"
pd.to_pickle(gene_count_vec_dict, gene_path)

## Building disease vector QE

In [161]:
disease2id_dict = build_field_qe_dict(
    df_col=df_qe_unique_gd["disease_qe"], 
    stop_words=STOP_WORDS, spacy_lm=sp
)

text: Pancreatic cancer Malignant tumor of pancreas Malignant tumor of pancreas (disorder) CA - Pancreatic cancer Pancreatic cancer CA - Cancer of pancreas Malignant tumour of pancreas Local recurrence of malignant tumor of pancreas Malignant neoplasm of ectopic pancreatic tissue Primary malignant neoplasm of pancreas Malignant tumor of endocrine pancreas Malignant tumor of tail of pancreas Secondary malignant neoplasm of pancreas Malignant tumor of head of pancreas Malignant tumor of exocrine pancreas Malignant tumor of body of pancreas Malignant neoplasm of intraabdominal organ Neoplasm of pancreas
text: Pancreatic adenocarcinoma    
text: Pancreatic ductal adenocarcinoma    
text: Pancreatic adenocarcinoma    
text: Lung cancer Malignant neoplasm lung: [of bronchus or lung NOS] or [lung cancer] Malignant neoplasm of bronchus or lung NOS Malignant neoplasm lung: [of bronchus or lung NOS] or [lung cancer] (disorder) Lung cancer  
text: Breast cancer Malignant tumor of breast Malignant

text: colorectal cancer    
text: melanoma Malignant melanoma Melanoma, NOS Malignant melanoma, morphology (morphologic abnormality) Malignant melanoma, no ICD-O subtype (morphologic abnormality) Melanoma Malignant melanoma, NOS MM - Malignant melanoma Malignant melanoma (morphologic abnormality) Malignant melanoma, no ICD-O subtype Necrotic melanoma Minimal deviation melanoma Choroidal melanoma, diffuse Neoplasm, malignant (primary) Malignant melanoma - category
text: melanoma Malignant melanoma Melanoma, NOS Malignant melanoma, morphology (morphologic abnormality) Malignant melanoma, no ICD-O subtype (morphologic abnormality) Melanoma Malignant melanoma, NOS MM - Malignant melanoma Malignant melanoma (morphologic abnormality) Malignant melanoma, no ICD-O subtype Necrotic melanoma Minimal deviation melanoma Choroidal melanoma, diffuse Neoplasm, malignant (primary) Malignant melanoma - category
text: melanoma Malignant melanoma Melanoma, NOS Malignant melanoma, morphology (morphologic 

text: melanoma Malignant melanoma Melanoma, NOS Malignant melanoma, morphology (morphologic abnormality) Malignant melanoma, no ICD-O subtype (morphologic abnormality) Melanoma Malignant melanoma, NOS MM - Malignant melanoma Malignant melanoma (morphologic abnormality) Malignant melanoma, no ICD-O subtype Necrotic melanoma Minimal deviation melanoma Choroidal melanoma, diffuse Neoplasm, malignant (primary) Malignant melanoma - category
text: melanoma Malignant melanoma Melanoma, NOS Malignant melanoma, morphology (morphologic abnormality) Malignant melanoma, no ICD-O subtype (morphologic abnormality) Melanoma Malignant melanoma, NOS MM - Malignant melanoma Malignant melanoma (morphologic abnormality) Malignant melanoma, no ICD-O subtype Necrotic melanoma Minimal deviation melanoma Choroidal melanoma, diffuse Neoplasm, malignant (primary) Malignant melanoma - category
text: melanoma Malignant melanoma Melanoma, NOS Malignant melanoma, morphology (morphologic abnormality) Malignant melan

text: acute myeloid leukemia Acute myeloid leukemia, disease Acute myeloid leukemia Acute myeloid leukemia Acute myeloid leukemia without mention of remission Acute myeloid leukaemia AML - Acute myeloid leukaemia Acute myelocytic leukemia Acute myelocytic leukaemia Acute myeloid leukemia Acute myeloid leukemia, disease (disorder) AML - Acute myeloblastic leukemia AML - Acute myeloblastic leukaemia AML - Acute myeloid leukemia Acute myeloid leukaemia, disease Acute non-lymphocytic leukemia Acute myeloblastic leukemia Acute myeloid leukaemia Acute myeloblastic leukaemia Acute myelocytic leukemia Acute myeloid leukaemia, no ICD-O subtype Acute myelocytic leukaemia Acute myeloid leukemia, no ICD-O subtype Acute myelogenous leukemia Acute myeloid leukemia, no ICD-O subtype (morphologic abnormality) Acute non-lymphocytic leukaemia Acute granulocytic leukaemia Acute granulocytic leukemia Acute myelogenous leukaemia Acute myeloid leukemia - category Acute myeloid leukaemia Acute myeloid leukae

text: cervical cancer    
text: colon cancer    
text: endometrial cancer    
text: pancreatic cancer Malignant tumor of pancreas Malignant tumor of pancreas (disorder) CA - Pancreatic cancer Pancreatic cancer CA - Cancer of pancreas Malignant tumour of pancreas Local recurrence of malignant tumor of pancreas Malignant neoplasm of ectopic pancreatic tissue Primary malignant neoplasm of pancreas Malignant tumor of endocrine pancreas Malignant tumor of tail of pancreas Secondary malignant neoplasm of pancreas Malignant tumor of head of pancreas Malignant tumor of exocrine pancreas Malignant tumor of body of pancreas Malignant neoplasm of intraabdominal organ Neoplasm of pancreas
text: breast cancer Malignant tumor of breast Malignant tumor of breast (disorder) Malignant tumour of breast Breast cancer CA - Breast cancer Malignant melanoma of breast Malignant neoplasm of breast lower inner quadrant Sarcoma of breast Hormone receptor positive malignant neoplasm of breast Malignant neoplasm 

In [ ]:
disease2id_dict

In [162]:
disease_count_vec_dict = build_field_count(
    df_col_text=df["brief_t_and_s"],
    df_col_id=df["doc_id"],
    field_dict=disease2id_dict, spacy_lm=sp
)


  2%|▏         | 838/40203 [00:19<11:37, 56.45it/s]


  5%|▍         | 1832/40203 [00:38<10:57, 58.32it/s]


  7%|▋         | 2852/40203 [00:57<10:23, 59.91it/s]


 10%|▉         | 3874/40203 [01:16<10:28, 57.80it/s]


 12%|█▏        | 4895/40203 [01:34<08:40, 67.77it/s]


...

 92%|█████████▏| 36955/40203 [11:46<01:15, 42.79it/s]


 94%|█████████▍| 37895/40203 [12:05<00:47, 48.18it/s]


 97%|█████████▋| 38834/40203 [12:23<00:28, 47.67it/s]


 99%|█████████▉| 39723/40203 [12:41<00:09, 48.02it/s]


100%|██████████| 40203/40203 [12:50<00:00, 52.15it/s]


In [163]:
disease_path = "../data/aspect_data/sample/disease_qe_word_vec.pickle"
pd.to_pickle(disease_count_vec_dict, disease_path)

In [170]:
disease_count_vec_dict

{'2017_18_NCT01774162': [0,
  1,
  1,
  1,
  3,
  0,
  0,
  0,
  0,
  1,
  0,
  3,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  3,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  

In [ ]:
break

In [100]:
sp = spacy.load('en_core_web_sm')

# https://spacy.io/usage/linguistic-features#native-tokenizer-additions
# https://github.com/explosion/spaCy/blob/master/spacy/util.py
infixes = list(sp.Defaults.infixes)

In [105]:
# https://github.com/explosion/spaCy/blob/master/spacy/lang/punctuation.py

from spacy.lang.char_classes import ALPHA, ALPHA_LOWER, ALPHA_UPPER
from spacy.lang.char_classes import CONCAT_QUOTES, LIST_ELLIPSES, LIST_ICONS
from spacy.util import compile_infix_regex

infixes = (
    LIST_ELLIPSES
    + LIST_ICONS
    + [
        r"(?<=[0-9])[+\-\*^](?=[0-9-])",
        r"(?<=[{al}{q}])\.(?=[{au}{q}])".format(
            al=ALPHA_LOWER, au=ALPHA_UPPER, q=CONCAT_QUOTES
        ),
        r"(?<=[{a}]),(?=[{a}])".format(a=ALPHA),
        # EDIT: commented out regex that splits on hyphens between letters:
        #r"(?<=[{a}])(?:{h})(?=[{a}])".format(a=ALPHA, h=HYPHENS),
        r"(?<=[{a}0-9])[:<>=/](?=[{a}])".format(a=ALPHA),
    ]
)

infix_re = compile_infix_regex(infixes)
sp.tokenizer.infix_finditer = infix_re.finditer

In [113]:
# text_test = df["brief_t_and_s"][36]
text_test = "hello-world this-is jerry; well what's going on bhere?"
text_test = "KRAS (G13D), BRAF-V600E amplification,"
text_test = df_qe["qe_all"][3][3]
text_sp = sp(text_test)
[w for w in text_sp]

[OSRC,
 PPP1R130,
 RB,
 p105-Rb,
 p110-RB1,
 pRb,
 pp110,
 BCC7,
 BMFS5,
 LFS1,
 P53,
 TRP53,
 ',
 C-K-RAS,
 C-K-RAS,
 CFC2,
 K-RAS2A,
 K-RAS2B,
 K-RAS4A,
 K-RAS4B,
 K-Ras,
 K-Ras,
 2,
 KI-RAS,
 KRAS1,
 KRAS2,
 NS,
 NS3,
 OES,
 RALD,
 RASK2,
 c-Ki-ras,
 c-Ki-ras2]

In [ ]:
text_sp[2].lemma_

In [ ]:
text_sp[0]
text_sp[2]

In [ ]:
tops.keys()

In [ ]:
tops[1][1].strip()

In [ ]:
tops[1][1].split(" ")